In [25]:
import sys
import os
import logging
import logging.config
import json
import shutil
import matplotlib as mpl
import matplotlib.pyplot as plt
import pickle as pkl

# mpl.use('Agg')

import numpy as np

import copy
import sqlite3
import git
import torch
import torchvision
import torch.autograd as autograd
import torch.nn as nn
import torch.nn.functional as F
import torch.optim as optim

from misc.database import Database

from prediction_model import utils
from prediction_model.models.lstm_l0 import L0SeqLSTM
from prediction_model.models.fully_connected_l0 import L0FCN
from prediction_model.models.ntm_aio_l0 import EncapsulatedNTML0
from prediction_model.models.ntm_aio import EncapsulatedNTM
from prediction_model.objectives.sse import SSE
from prediction_model.objectives.logistic_loss import LogisticLoss

# plotting tools
from bokeh.io import output_notebook, show
from bokeh.layouts import gridplot
from bokeh.plotting import figure
from bokeh.models import CustomJS, Slider, ColumnDataSource, Whisker, Range1d

from datetime import datetime
from types import SimpleNamespace

output_notebook()

Loading BokehJS ...

In [6]:
def model_forward_fcn(X_train, y_train, model_p, objective_p, optimizer_p, l0_reg, backward=True, enable_gpu=False):
    model_out = []
    total_log_loss = None
    total_penalty = None
    
    X_train = torch.FloatTensor(X_train)
    y_train = torch.FloatTensor(y_train)
    if enable_gpu:
        X_train = X_train.cuda()
        y_train = y_train.cuda()

    out, (hidden, penalty) = model_p.forward(X_train)
#         ht, ct = hidden
    # print(x_t1, out)
    out = torch.clamp(out, -8, 8)
    out = F.sigmoid(out)
    # print(out)

#     print(out.shape)
#     print(y_train.shape)
    log_loss = objective_p(out, y_train)

    if total_log_loss is None:
        total_log_loss = log_loss
        total_penalty = penalty
    else:
        total_log_loss += log_loss
        total_penalty += penalty

    model_out.append(out.cpu().data.numpy())

    total_loss = total_log_loss + l0_reg * total_penalty

    if backward:
        model.zero_grad()
        total_loss.backward()
        optimizer_p.step()

    if backward:
        total_penalty = np.sum(total_penalty.cpu().data.numpy())

    return model, \
           (np.sum(total_log_loss.cpu().data.numpy()), total_penalty), \
           model_out

In [7]:
def logistic_map(x, alpha):
    return alpha*x*(1-x)

def linear_map(x, alpha):
    return alpha*x

In [ ]:
seed = 0
alpha = 1
enable_gpu = True
l0_reg = 0.001

# for seed in range(args.n_seeds):
utils.common.set_global_seeds(seed)

model = L0FCN(input_bins=1,
              output_bins=1,
              fc_config=[20]*2,
              enable_gpu=True,
              test_mode=False)

if enable_gpu:
    model = model.cuda()

optimizer = optim.Adam(model.parameters(),
                       lr=1e-4,
                       weight_decay=0)

objective = SSE()

prev_loss = 0
epoch = 0
best_model = None
best_acc = 100
best_nparams = 0

while True:
    X_train = np.random.rand(50)
    y_train = np.array(list(map(lambda x: logistic_map(x, alpha), X_train)))

    X_train = X_train.reshape((-1, 1))
    y_train = y_train.reshape((-1, 1))

    model.train()
    model, (log_loss, penalty), model_out = model_forward_fcn(X_train,
                                                              y_train,
                                                              model,
                                                              objective,
                                                              optimizer,
                                                              l0_reg,
                                                              enable_gpu=enable_gpu)
    total_loss = (log_loss + l0_reg * penalty)

    # Validation
    model.eval()

    _, _, model_out = model_forward_fcn(X_train,
                                        y_train,
                                        model,
                                        objective,
                                        optimizer,
                                        l0_reg,
                                        enable_gpu=enable_gpu,
                                        backward=False)
#     predictions = (np.array(model_out) > 0.5).astype(int)
    predictions = np.array(model_out).flatten()
    actual = y_train.flatten()
    # print(actual == predictions)
    accuracy = np.sum(actual == predictions) / len(actual)
    model_nparams = model.get_l0_norm()

    # if accuracy > best_acc or (accuracy == best_acc and best_nparams > model_nparams):
    if log_loss <= best_acc and not (np.isnan(log_loss) or np.isnan(penalty)):
        best_model = copy.deepcopy(model.state_dict())
        best_acc = log_loss
        best_nparams = model_nparams
    div = X_train.shape[0]
    # print diagnostics
    if epoch % 100 == 0:
        model_out = np.array(model_out).flatten()
        print("")
        print("epoch: {} SSE loss: {}, l0 penalty: {} total loss: {}".format(epoch,
                                                                              log_loss / div,
                                                                              penalty / div,
                                                                              total_loss))
        print("accuracy: {}, actual: {}, predicted: {}, n_params: {} model_out: {}".format(accuracy,
                                                                                                 X_train.flatten(),
                                                                                                 predictions,
                                                                                                 model.get_l0_norm(),
                                                                                                 model_out))

    if np.abs(total_loss - prev_loss) <= 1e-9:
        print("Training converged: {}".format(np.abs(total_loss - prev_loss)))
        break

    prev_loss = total_loss
    epoch += 1

    if np.isnan(log_loss) or np.isnan(penalty):
        print("NaN detected")
        break
#     break

fc0
Gate mode: unique
fc1
Gate mode: unique
Gate mode: unique

epoch: 0 SSE loss: 0.10524124145507813, l0 penalty: 8.002297973632812 total loss: 5.662176971435547
accuracy: 0.0, actual: [0.5488135  0.71518937 0.60276338 0.54488318 0.4236548  0.64589411
 0.43758721 0.891773   0.96366276 0.38344152 0.79172504 0.52889492
 0.56804456 0.92559664 0.07103606 0.0871293  0.0202184  0.83261985
 0.77815675 0.87001215 0.97861834 0.79915856 0.46147936 0.78052918
 0.11827443 0.63992102 0.14335329 0.94466892 0.52184832 0.41466194
 0.26455561 0.77423369 0.45615033 0.56843395 0.0187898  0.6176355
 0.61209572 0.616934   0.94374808 0.6818203  0.3595079  0.43703195
 0.6976312  0.06022547 0.66676672 0.67063787 0.21038256 0.1289263
 0.31542835 0.36371077], predicted: [0.4910428  0.49057236 0.4908599  0.49105614 0.49139714 0.49071363
 0.4913607  0.49023575 0.49009866 0.49150643 0.49042645 0.4911103
 0.49097762 0.49017122 0.49235564 0.49231192 0.49249384 0.49034846
 0.49045232 0.49027723 0.49007136 0.4904123 


epoch: 500 SSE loss: 0.08815521240234375, l0 penalty: 7.97047607421875 total loss: 4.806284423828125
accuracy: 0.0, actual: [0.8812033  0.53122103 0.8680575  0.77755907 0.96932112 0.92571412
 0.16927561 0.57996402 0.02856338 0.68828411 0.54150551 0.14278145
 0.66640611 0.36708941 0.09459162 0.00299151 0.60631975 0.79011012
 0.47399445 0.36391856 0.75603037 0.0063267  0.80624946 0.14631303
 0.2934198  0.61383733 0.8059898  0.14708033 0.66029159 0.40847581
 0.25638414 0.39374154 0.38463804 0.83570583 0.53699062 0.84165466
 0.16601442 0.83759583 0.3109018  0.71662891 0.49894272 0.59874476
 0.64255778 0.64013713 0.93336891 0.68057536 0.57611589 0.27045168
 0.83392349 0.2913378 ], predicted: [0.47267935 0.4732891  0.4726977  0.4728248  0.47256207 0.47261703
 0.47463748 0.47313565 0.4750991  0.4729502  0.47325674 0.47474164
 0.47298092 0.4738727  0.47491825 0.47516906 0.47306532 0.4728071
 0.47346926 0.47388488 0.47285497 0.4751599  0.47278446 0.47472772
 0.4741549  0.47305474 0.47278482 0.


epoch: 1000 SSE loss: 0.08775465965270995, l0 penalty: 7.94111083984375 total loss: 4.784788524627686
accuracy: 0.0, actual: [0.30764535 0.06200521 0.98878508 0.7190903  0.75756964 0.26375811
 0.81423212 0.56902059 0.45944772 0.13070624 0.31822656 0.3471398
 0.04941394 0.96384525 0.96475062 0.1106671  0.33928814 0.56340746
 0.48681865 0.56492329 0.86105383 0.81537125 0.41010138 0.52310581
 0.18856046 0.45604781 0.76245352 0.25340822 0.24580262 0.99679214
 0.22599421 0.962532   0.24860247 0.71298981 0.04488238 0.67372927
 0.41643382 0.51367789 0.51061752 0.37990148 0.01794764 0.80771941
 0.41246825 0.28481926 0.89542746 0.51598704 0.98335094 0.4560161
 0.71131126 0.09003222], predicted: [0.44920164 0.44989774 0.44760108 0.4481951  0.4481208  0.4493266
 0.44801128 0.44848505 0.44876957 0.4497045  0.44917148 0.44908923
 0.44993317 0.4477223  0.44772053 0.44976082 0.44911155 0.4484959
 0.44869164 0.448493   0.44792086 0.44800907 0.44891    0.44858837
 0.44954064 0.44877923 0.44811133 0.44


epoch: 1500 SSE loss: 0.052677912712097166, l0 penalty: 7.913941650390625 total loss: 3.02959271812439
accuracy: 0.0, actual: [0.24392333 0.65495435 0.35150695 0.62498055 0.03401694 0.24540688
 0.22322093 0.0760436  0.83643934 0.88957214 0.18126889 0.78185092
 0.59343407 0.1847256  0.37908656 0.9475536  0.01381148 0.47050336
 0.78318807 0.62917569 0.36378382 0.02195515 0.8975815  0.50285664
 0.29962934 0.04863477 0.9932151  0.81687624 0.16885527 0.88573366
 0.06075629 0.8205812  0.25389633 0.99687541 0.04379909 0.15060614
 0.78009182 0.02238677 0.13359511 0.23338146 0.22705116 0.39122358
 0.77979902 0.18917251 0.32549157 0.44852835 0.3491879  0.64779936
 0.98710881 0.02330982], predicted: [0.41055182 0.40802258 0.40989172 0.4082081  0.4118406  0.4105427
 0.41067883 0.41158244 0.4068905  0.40642864 0.41093636 0.40723565
 0.40840343 0.41091514 0.4097226  0.40556988 0.41196468 0.409162
 0.40722728 0.4081821  0.40981644 0.41191468 0.40630996 0.4089637
 0.41020995 0.41175076 0.40488216 0.4


epoch: 2000 SSE loss: 0.039977831840515135, l0 penalty: 7.888450317382812 total loss: 2.3933141078948976
accuracy: 0.0, actual: [0.53525707 0.90404425 0.50239657 0.10087001 0.52758198 0.71122893
 0.31295428 0.05032535 0.12328206 0.77969075 0.94802187 0.71818603
 0.75389358 0.10964897 0.63814993 0.28945067 0.361702   0.00315978
 0.04352426 0.79419409 0.77746827 0.56411938 0.38736774 0.34514564
 0.41004102 0.06705749 0.97356847 0.06405922 0.10844153 0.47859636
 0.87148378 0.98030973 0.67780738 0.87716066 0.26757641 0.61586974
 0.44980164 0.61761576 0.80281463 0.03813337 0.29641567 0.33406014
 0.50907489 0.74504766 0.59307464 0.34360118 0.30266013 0.27967976
 0.92107048 0.87532113], predicted: [0.3529567  0.34606403 0.35338718 0.35866645 0.35305724 0.3504048
 0.35587364 0.35933346 0.35837087 0.3493985  0.34487417 0.3503037
 0.34978524 0.35855064 0.35146713 0.35618263 0.35523304 0.35995638
 0.35942325 0.34901768 0.34944317 0.35254478 0.354896   0.35545057
 0.3545984  0.35911262 0.3441839 

...


epoch: 224700 SSE loss: 0.0007038623094558716, l0 penalty: 2.1549462890625 total loss: 0.1429404299259186
accuracy: 0.0, actual: [0.74681769 0.64160634 0.80226784 0.83552149 0.7518208  0.22009868
 0.00754541 0.5524171  0.8707866  0.2347144  0.14496289 0.62208556
 0.44407737 0.87400776 0.73175332 0.99383705 0.8585088  0.56170264
 0.23420617 0.07058532 0.42408932 0.33635656 0.88742915 0.47247018
 0.12665112 0.59784189 0.33217342 0.65105643 0.350031   0.94101862
 0.45074425 0.00964146 0.91479499 0.81023568 0.26034844 0.03625184
 0.0747244  0.00889796 0.88569589 0.68788494 0.55946646 0.58460872
 0.84636687 0.92708644 0.82466193 0.51156326 0.20385987 0.76899278
 0.07333884 0.3664727 ], predicted: [0.14817071 0.20895366 0.12247439 0.1089755  0.14568076 0.14256983
 0.03331978 0.22607562 0.09610423 0.15589122 0.08727475 0.21753389
 0.22861628 0.09499884 0.1558807  0.06123227 0.10042351 0.22585882
 0.15541144 0.05217151 0.22908723 0.21810673 0.09051479 0.22794853
 0.07703432 0.22419487 0.21747


epoch: 225200 SSE loss: 0.0006711339950561524, l0 penalty: 2.151875762939453 total loss: 0.14115048789978027
accuracy: 0.0, actual: [0.61316966 0.90404794 0.00226708 0.05895918 0.82994118 0.25618815
 0.8758846  0.44012528 0.98210729 0.36898972 0.33782189 0.66828238
 0.35285722 0.82763997 0.16146633 0.71534472 0.00414352 0.95191464
 0.32159874 0.42329418 0.52841904 0.76536149 0.41935195 0.59472579
 0.2738179  0.21234783 0.59354114 0.0116506  0.27044298 0.66774007
 0.64857156 0.29878445 0.41889115 0.69317678 0.80050992 0.59329958
 0.1602678  0.93547738 0.93760486 0.72921897 0.07207522 0.29098904
 0.20412905 0.23274887 0.1245308  0.54575026 0.20992994 0.01452019
 0.89203834 0.05221873], predicted: [0.21989898 0.08395042 0.0318035  0.04770812 0.1097798  0.17670305
 0.09304335 0.22863518 0.06282431 0.22271428 0.21800171 0.19070573
 0.22026603 0.11068388 0.09703822 0.16328996 0.0322365  0.070333
 0.2155774  0.22903004 0.22657171 0.13772638 0.22912256 0.22462524
 0.19595133 0.13531134 0.2247


epoch: 225700 SSE loss: 0.001450643688440323, l0 penalty: 2.1489108276367186 total loss: 0.17997772580385207
accuracy: 0.0, actual: [0.92233281 0.39453439 0.49162772 0.09596779 0.00390805 0.99698613
 0.91237413 0.01433987 0.95463575 0.8776768  0.14575624 0.96741414
 0.88639833 0.62260092 0.17305742 0.11188295 0.94300608 0.73713602
 0.58781744 0.55674247 0.60837492 0.82658779 0.92624927 0.42800434
 0.55917081 0.33318011 0.22433574 0.51614289 0.58196829 0.98760327
 0.54719037 0.83904673 0.05563249 0.36343339 0.74705049 0.14047938
 0.15034501 0.16782579 0.97821682 0.59270768 0.93704843 0.07973174
 0.80842504 0.07013382 0.46205745 0.89311855 0.10572066 0.55981261
 0.97189015 0.41272266], predicted: [0.07826048 0.22613642 0.22714789 0.06184188 0.03209382 0.05916295
 0.08119905 0.03460268 0.06938715 0.0922377  0.08724742 0.06614104
 0.08934233 0.21668617 0.1048988  0.06910326 0.072469   0.15169595
 0.22491288 0.22563319 0.22093768 0.11094399 0.07713173 0.22863477
 0.22557686 0.21683753 0.14


epoch: 226200 SSE loss: 0.0011449430137872695, l0 penalty: 2.1462142944335936 total loss: 0.16455786541104317
accuracy: 0.0, actual: [0.47901776 0.89433466 0.67347219 0.67627301 0.01849628 0.87989158
 0.55130272 0.87069268 0.36605797 0.8201543  0.25729045 0.3330589
 0.5798996  0.51580247 0.35018991 0.25347215 0.96024384 0.22975528
 0.40304283 0.8654771  0.71911406 0.04542259 0.56449193 0.1921669
 0.68877916 0.27801324 0.26366685 0.30501943 0.1465308  0.06124924
 0.39156007 0.61364238 0.4539646  0.98877942 0.51941834 0.39582624
 0.86122264 0.28396269 0.60226117 0.12709846 0.17110184 0.54083308
 0.16644504 0.04049433 0.99586373 0.05569849 0.91716878 0.09645481
 0.04658641 0.8419268 ], predicted: [0.22597758 0.08525927 0.18568443 0.18397507 0.03470735 0.08993414
 0.22429319 0.09303083 0.21985136 0.11180227 0.17606615 0.21489583
 0.22362931 0.22511931 0.21745822 0.17206752 0.06661294 0.1488298
 0.22550234 0.09482881 0.15933554 0.04216839 0.22398683 0.11716831
 0.1764912  0.19904456 0.1829


epoch: 226700 SSE loss: 0.0004059664160013199, l0 penalty: 2.143065185546875 total loss: 0.12745158007740975
accuracy: 0.0, actual: [0.05591469 0.67422291 0.51607561 0.05111632 0.02159931 0.42138699
 0.76544106 0.18993558 0.41993543 0.95274477 0.97173226 0.23411751
 0.32103208 0.29927517 0.79824079 0.54416411 0.20145573 0.74157241
 0.89568006 0.89335757 0.95698447 0.51303001 0.64623378 0.47581709
 0.38234943 0.89622653 0.80604621 0.4299301  0.27775219 0.37148734
 0.19263108 0.35649766 0.91172354 0.72695969 0.85698115 0.51361539
 0.05146891 0.38685783 0.70528201 0.79265064 0.83238278 0.86000165
 0.44976023 0.64173261 0.44841761 0.84118397 0.29619508 0.85146397
 0.06013223 0.89869274], predicted: [0.04653468 0.1901907  0.22793044 0.04496365 0.0363586  0.2301114
 0.1398241  0.11767051 0.23014493 0.07093947 0.06605414 0.15564051
 0.21624921 0.21305834 0.12465504 0.2272863  0.12692422 0.1518114
 0.0876922  0.08844465 0.06982049 0.22800037 0.20819144 0.22885594
 0.22542734 0.08751602 0.1212

In [15]:
model_test = L0FCN(input_bins=1,
                  output_bins=1,
                  fc_config=[20]*2,
                  enable_gpu=True,
                  test_mode=False)
model_test.load_state_dict(best_model)

fc0
Gate mode: unique
fc1
Gate mode: unique
Gate mode: unique


<All keys matched successfully>

In [16]:
model_test.get_l0_norm()

tensor(36)

In [28]:
model_test = model_test.cuda()

model.eval()

x = np.arange(0, 1, 0.01)
y = list(map(lambda val: logistic_map(val, alpha), x))
y_pred = None
k = 1
for i in range(k):
    y_pred_k = []
    for x_val in x:
        x_val = torch.FloatTensor([x_val]).cuda()
        out, _ = model_test.forward(x_val)
        out = torch.clamp(out, -8, 8)
        out = F.sigmoid(out)
        y_pred_k.append(out.data.cpu().numpy()[0])
    
    if y_pred is None:
        y_pred = np.array(y_pred_k)
    else:
        y_pred += np.array(y_pred_k)

y_pred = y_pred/k
plot_options = dict(width=900,
                    plot_height=450,
                    tools='pan,wheel_zoom,reset,save')

plot = figure(**plot_options)
plot.line(x,
          y)
plot.line(x,
          y_pred,
         line_color="orange")
plot.x(X_train.flatten(),
       y_train.flatten())

plot.xaxis.axis_label = 'x'
plot.yaxis.axis_label = 'f(x)'

show(plot)

In [29]:
series_pred = []
series_pred_in = []
series_actual = []
lambda_series_pred = []
lambda_series_actual = []
x_t_m = 0.7
x_t_a = x_t_m
x_t_i = x_t_m
n_points = 500

step = 0
tot_steps = 5

for i in range(n_points):
    x_val = torch.FloatTensor([x_t_m]).cuda()
    out, _ = model_test.forward(x_val)
    out = torch.clamp(out, -8, 8)
    out = F.sigmoid(out)
    lambda_series_pred.append(out.data.cpu().numpy()[0]/(x_t_m*(1-x_t_m)))
    x_t_m = out.data.cpu().numpy()[0]
    series_pred.append(x_t_m)
    
    if step >= tot_steps:
        x_t_i = x_t_a
        step = 0
    
    x_val = torch.FloatTensor([x_t_i]).cuda()
    out, _ = model_test.forward(x_val)
    out = torch.clamp(out, -8, 8)
    out = F.sigmoid(out)
    x_t_i = out.data.cpu().numpy()[0]
    series_pred_in.append(x_t_i)
    step += 1
    
    lambda_series_actual.append(logistic_map(x_t_a, alpha=alpha)/(x_t_a*(1-x_t_a)))
    x_t_a = logistic_map(x_t_a, alpha=alpha)
    series_actual.append(x_t_a)

plot_options = dict(width=900,
                    plot_height=450,
                    tools='pan,xwheel_zoom,reset,save')

plot = figure(**plot_options)
plot.line(range(n_points),
          series_actual)
plot.line(range(n_points),
          series_pred,
          line_color="orange")
plot.line(range(n_points),
          series_pred_in,
          line_color="red")

plot.xaxis.axis_label = 'step'
plot.yaxis.axis_label = 'f(x)'

plot.y_range = Range1d(0, 1)

show(plot)

mean_lambda_pred = [ np.mean(lambda_series_pred[:i]) 
                    for i in range(1, len(lambda_series_pred)) ]

plot = figure(**plot_options)
plot.line(range(n_points),
          lambda_series_actual)
plot.line(range(n_points),
          lambda_series_pred,
          line_color="orange")
plot.line(range(n_points),
          mean_lambda_pred,
          line_color="red")

plot.xaxis.axis_label = 'step'
plot.yaxis.axis_label = 'lambda'

show(plot)

In [30]:
n_points = 500

step = 0
tot_steps = 10
step_stderr = []

for step in range(1, tot_steps):
    print(step)
    step_err = []
    for i in range(n_points):  
        x_t_m = series_actual[i]
        err = []
        for pred_step in range(step):
            x_val = torch.FloatTensor([x_t_m]).cuda()
            out, _ = model_test.forward(x_val)
            out = torch.clamp(out, -8, 8)
            out = F.sigmoid(out)
            lambda_series_pred.append(out.data.cpu().numpy()[0]/(x_t_m*(1-x_t_m)))
            x_t_m = out.data.cpu().numpy()[0]
            
            try:
                err.append(np.abs(series_actual[i+pred_step+1] - x_t_m))
            except IndexError:
                break
        step_err.append(np.mean(err))
    step_err = np.array(step_err)
    step_err = step_err[~np.isnan(step_err)]
    step_stderr.append(np.mean(np.array(step_err)))
#     print(step_err)
#     print(step_stderr)
            
plot_options = dict(width=900,
                    plot_height=450,
                    tools='pan,xwheel_zoom,reset,save')

plot = figure(**plot_options)
plot.line(range(tot_steps),
          step_stderr,
         line_width=2)

plot.xaxis.axis_label = 'prediction steps'
plot.yaxis.axis_label = 'standard_error'

show(plot)

1
2
3
4
5
6
7
8
9


In [ ]:
step_stderr